In [11]:
'''
Author - Siddhesh Birari
Last Modified - 4/16/2022
Description - Feature Engineering on WPIP_PR_CURR_WIDE
Note - Please call function in the below order in which they are defined exclude load_data function for call.
'''
class Wpip:
    
    
    def import_libraries(): #Import Libraries / packages
        global pd,np,stats,date
        import pandas as pd
        import numpy as np
        import scipy.stats as stats
        from datetime import date
        from pandas_profiling import ProfileReport
        from IPython.core.display import display
        print("Imported necessary libraries")    
    
    def load_data(): #Load data. Future State - Getting data directly from Database rather than flat files
        Wpip.import_libraries()
        print("\nLoading data in dataframe") 
        WPIP_Path = r"C:\Citizens Work Specific\Work - To Make Positive Impact\Feature Engineering\Dataset\wpip_pr_curr_wide_202204151242.csv"
        Wpip.import_libraries()
        global df_WPIP_Copy
        df_WPIP_Copy = pd.read_csv(WPIP_Path)
            
    def copy_dataframe(): #Backing up dataframe
        Wpip.load_data()
        print("\nBacking up data in dataframe") 
        global df_WPIP
        df_WPIP = df_WPIP_Copy.copy()
        return df_WPIP
        
    def display_column_datatype(): #Getting columns and datatypes
        Wpip.copy_dataframe()
        i = 0
        for col in df_WPIP.columns:
            print(i,col,'\t\t\t\t\t',df_WPIP[df_WPIP.columns[i]].dtype)
            i = i + 1
        print("Final number of columns in this dataframe is :",i-1)
           
    def handle_missing_data(df_WPIP): #Handle missing data. Imputation,Encoding needs to be done. 
        Wpip.copy_dataframe()
        threshold = 0.8
        global columns_to_be_deleted
        columns_to_be_deleted = df_WPIP.columns[df_WPIP.isnull().mean() > threshold]
        df_WPIP = df_WPIP[df_WPIP.columns[df_WPIP.isnull().mean() < threshold]] #Delete columns with duplicates more than threshold
        df_WPIP = df_WPIP.loc[df_WPIP.isnull().mean(axis=1) < threshold] #Delete rows
        global df_WPIP_after_missing
        df_WPIP_after_missing = df_WPIP.copy()
        return df_WPIP
    
    def update_datatypes(df_WPIP): #Updating datatypes
        Wpip.handle_missing_data(df_WPIP) 
        df_WPIP['month'] = df_WPIP['month'].astype(int)
        df_WPIP['year'] = df_WPIP['year'].astype(int)
        return df_WPIP
    
    def feature_addition(df_WPIP): #Add features for wide data analysis
        df_WPIP['Z_deposit_balance'] = stats.zscore(df_WPIP['deposit_balance'])
        df_WPIP['Z_total_revenue'] = stats.zscore(df_WPIP['total_revenue'])
        df_WPIP['Year_Month'] = df_WPIP['year'].map(str)+ '-' + df_WPIP['month'].map(str)
        df_WPIP['Year_Month_Quarter'] = pd.to_datetime(df_WPIP['Year_Month'].values, format='%Y-%m').astype('period[Q]')
        df_WPIP['Customer_Since_Days'] = (date.today()) - (pd.to_datetime(df_WPIP['customer_since'],format="%Y-%m-%d").dt.date)
        return df_WPIP
    
    def drop_columns(df_WPIP):
        #Deleting columns if unique values are less than threshold
        columns_to_inspect_unique = ['profitability_group_name','cust_state_cd','group_nm','naics_code','naics_description','pm_division_executive_name',
         'pm_regional_manager_name','pm_team_leader_name','portfolio_manager_name','pov_conc_align','pov_concentration',
         'pov_division_name','pov_lob_name','pov_name','pov_sub_lob1','pov_sub_lob2','relationship_manager_name',
         'rm_division_executive_emp_num','rm_division_executive_name','rm_emp_num','rm_group_head_name','rm_team_lead_emp_num'
        ,'rm_unit_executive_name']
        length = len(columns_to_inspect_unique)
        for i in range(length):
            if (len(df_WPIP[columns_to_inspect_unique[i]].unique()) <= 12):  
                print("Column :",df_WPIP[[columns_to_inspect_unique[i]]].columns[0],"Has unique count",len(df_WPIP[columns_to_inspect_unique[i]].unique()))
                print("Column is being dropped from dataframe")
                df_WPIP.drop(df_WPIP[[columns_to_inspect_unique[i]]].columns[0],axis=1,inplace=True)
        #Delete columns if aren't required from business perspective        
        identifiers_can_be_deleted = ['as_of_dt','c&i flag','cre_composite','customer_since','naics_code','naics_code_reference_id',
                              'naics_description','oblig_count','officer_id','pm_regional_manager_name','pm_team_leader_name',
                              'portfolio_manager_hierarchy_id','portfolio_manager_name','pov_operating_segment'
                              ,'pov_sub_lob1','pov_sub_lob2','prior_month_risk_rating_id','prior_month_rptng_ord','prior_quarter_risk_rating_id',
                              'prior_quarter_rptng_ord','profitability_group_name','rc_lgl_hrchy_id','rc_lob_hrchy_id','relationship_group_crm_id',
                              'relationship_group_id','relationship_group_name','relationship_manager_name','reporting_dt','risk_classification_cd',
                              'risk_rating_id','rm_division_executive_emp_num','rm_division_executive_name','rm_emp_num','rm_group_head_emp_num',
                              'rm_team_lead_emp_num','rm_team_lead_name','rm_unit_executive_emp_num','rptng_order_num','wgtd_risk_rating_rt']
        df_WPIP.drop(df_WPIP[identifiers_can_be_deleted].columns,axis=1,inplace=True)
        return df_WPIP
    
    def profile_report(df_WPIP): #Get detailed report and visualization for analysis
        return df_WPIP[df_WPIP.columns[df_WPIP.columns.isin(["card_revenue","cash_management_revenue","cashmanagement_non_interest_income","deposit_balance","deposit_revenue","total_expenses","total_revenue"])]].profile_report()
        
          

In [14]:
df_WPIP = Wpip.copy_dataframe()
df_WPIP = Wpip.handle_missing_data(df_WPIP)
df_WPIP = Wpip.update_datatypes(df_WPIP)
df_WPIP = Wpip.feature_addition(df_WPIP)
df_WPIP = Wpip.drop_columns(df_WPIP)
df_WPIP.head()

Imported necessary libraries

Loading data in dataframe
Imported necessary libraries

Backing up data in dataframe
Imported necessary libraries

Loading data in dataframe
Imported necessary libraries

Backing up data in dataframe
Imported necessary libraries

Loading data in dataframe
Imported necessary libraries

Backing up data in dataframe
Column : group_nm Has unique count 2
Column is being dropped from dataframe
Column : pm_division_executive_name Has unique count 7
Column is being dropped from dataframe
Column : pov_conc_align Has unique count 2
Column is being dropped from dataframe
Column : pov_concentration Has unique count 11
Column is being dropped from dataframe
Column : pov_division_name Has unique count 7
Column is being dropped from dataframe
Column : pov_lob_name Has unique count 12
Column is being dropped from dataframe
Column : pov_name Has unique count 2
Column is being dropped from dataframe
Column : rm_group_head_name Has unique count 3
Column is being dropped from

alll_amt  alloc_exp_overhead_amt  alloc_exp_product_amt  \
0       0.0                    1.74                  42.80   
1       0.0                    1.87                  46.00   
2       0.0                    1.91                  47.13   
3       0.0                    1.94                  47.67   
4       0.0                    1.96                  48.17   

   capital_ben_apportioned_amt  capital_benefit_amt  capital_markets  \
0                          0.0                  0.0              0.0   
1                          0.0                  0.0              0.0   
2                          0.0                  0.0              0.0   
3                          0.0                  0.0              0.0   
4                          0.0                  0.0              0.0   

   capital_markets_rfnd  card_revenue  cash_management_revenue  \
0                   0.0           0.0                      0.0   
1                   0.0           0.0                      0.0   
2                   0.0           0.0                      0.0   
3                   0.0           0.0                      0.0   
4                   0.0           0.0                      0.0   

   cashmanagement_non_interest_income  ...  utilization$  \
0                                 0.0  ...           0.0   
1                                 0.0  ...           0.0   
2                                 0.0  ...           0.0   
3                                 0.0  ...           0.0   
4                                 0.0  ...           0.0   

   wpi_client_sales_amt  party_ctzns_restruct_mgmt_ind  month  year  \
0                   0.0                            0.0      3  2019   
1                   0.0                            0.0      5  2019   
2                   0.0                            0.0      8  2019   
3                   0.0                            0.0      9  2019   
4                   0.0                            0.0      7  2019   

   Z_deposit_balance  Z_total_revenue  Year_Month  Year_Month_Quarter  \
0          -0.180268        -0.055037      2019-3              2019Q1   
1          -0.176940        -0.054511      2019-5              2019Q2   
2          -0.174279        -0.054325      2019-8              2019Q3   
3          -0.163845        -0.054236      2019-9              2019Q3   
4          -0.172625        -0.054154      2019-7              2019Q3   

   Customer_Since_Days  
0             803 days  
1             803 days  
2             803 days  
3             803 days  
4             803 days  

[5 rows x 230 columns]

In [15]:
Wpip.profile_report(df_WPIP)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [5]:
df_WPIP.sort_values(by='Z_deposit_balance', ascending=False)

alll_amt  alloc_exp_overhead_amt  alloc_exp_product_amt  \
923      0.00                    0.00                   0.00   
924      0.00                    0.00                   0.00   
925      0.00                    0.00                   0.00   
933      0.00                    0.00                   0.00   
934      0.00                    0.00                   0.00   
..        ...                     ...                    ...   
636      0.00                    0.00                   0.01   
377      0.00                    4.38                 107.51   
856      0.00                   10.40                 255.24   
397      0.00                   20.67                 507.27   
621  20703.22                   54.17                1331.32   

     capital_ben_apportioned_amt  capital_benefit_amt  capital_markets  \
923                  6152.730585             73832.77              0.0   
924                  6085.147451             73021.77              0.0   
925                  6017.625868             72211.51              0.0   
933                  5287.510815             63450.13              0.0   
934                  5229.057695             62748.69              0.0   
..                           ...                  ...              ...   
636                     0.000000                 0.00              0.0   
377                     0.000000                 0.00              0.0   
856                     0.000000                 0.00              0.0   
397                     0.000000                 0.00              0.0   
621                   226.572610              2718.87              0.0   

     capital_markets_rfnd  card_revenue  cash_management_revenue  \
923                   0.0           0.0                     0.00   
924                   0.0           0.0                     0.00   
925                   0.0           0.0                     0.00   
933                   0.0           0.0                     0.00   
934                   0.0           0.0                     0.00   
..                    ...           ...                      ...   
636                   0.0           0.0                     0.00   
377                   0.0           0.0                   327.05   
856                   0.0           0.0                   777.05   
397                   0.0           0.0                  1540.68   
621                   0.0           0.0                  1661.64   

     cashmanagement_non_interest_income  ...  utilization$  \
923                                0.00  ...           0.0   
924                                0.00  ...           0.0   
925                                0.00  ...           0.0   
933                                0.00  ...           0.0   
934                                0.00  ...           0.0   
..                                  ...  ...           ...   
636                                0.00  ...           0.0   
377                              327.05  ...           0.0   
856                              777.05  ...           0.0   
397                             1540.68  ...           0.0   
621                             1661.64  ...           0.0   

     wpi_client_sales_amt  party_ctzns_restruct_mgmt_ind  month  year  \
923                   0.0                            0.0     12  2019   
924                   0.0                            0.0      1  2020   
925                   0.0                            0.0      2  2020   
933                   0.0                            0.0      3  2020   
934                   0.0                            0.0      4  2020   
..                    ...                            ...    ...   ...   
636                   0.0                            0.0      7  2019   
377                   0.0                            0.0      3  2019   
856                   0.0                            0.0      4  2019   
397           129687000.0                            0.